In [1]:
# @title Get Video
!wget -P video/ "https://ml-hiring.fringecore.sh/waiter_calling/desk_video.mp4"

--2025-07-05 21:00:27--  https://ml-hiring.fringecore.sh/waiter_calling/desk_video.mp4
Resolving ml-hiring.fringecore.sh (ml-hiring.fringecore.sh)... 104.21.75.216, 172.67.182.61, 2606:4700:3031::6815:4bd8, ...
Connecting to ml-hiring.fringecore.sh (ml-hiring.fringecore.sh)|104.21.75.216|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 4410526 (4.2M) [video/mp4]
Saving to: ‘video/desk_video.mp4’

desk_video.mp4      100%[===================>]   4.21M  --.-KB/s    in 0.07s   

2025-07-05 21:00:27 (57.0 MB/s) - ‘video/desk_video.mp4’ saved [4410526/4410526]



In [2]:
!gdown --folder https://drive.google.com/drive/folders/1oXAReQlbOhZJGuWwrKf-b_fYDe9Lg5Uu?usp=sharing

Retrieving folder contents
Processing file 1M6hxuiEbJWN6-EsRLqgkBFTTgQf3scCk obj.names
Processing file 1KeEhQRjLp8SX7cnEpHcWCaiUVDk3LW2P yolov4-obj.cfg
Processing file 1wezrriLCb3GcYzv3QZW4IaEiGe0jk4EW yolov4-obj_best.weights
Retrieving folder contents completed
Building directory structure
Building directory structure completed
Downloading...
From: https://drive.google.com/uc?id=1M6hxuiEbJWN6-EsRLqgkBFTTgQf3scCk
To: /content/waiter_calling_model/obj.names
100% 59.0/59.0 [00:00<00:00, 402kB/s]
Downloading...
From: https://drive.google.com/uc?id=1KeEhQRjLp8SX7cnEpHcWCaiUVDk3LW2P
To: /content/waiter_calling_model/yolov4-obj.cfg
100% 13.4k/13.4k [00:00<00:00, 61.9MB/s]
Downloading...
From (original): https://drive.google.com/uc?id=1wezrriLCb3GcYzv3QZW4IaEiGe0jk4EW
From (redirected): https://drive.google.com/uc?id=1wezrriLCb3GcYzv3QZW4IaEiGe0jk4EW&confirm=t&uuid=6031ba7a-b9e8-4c1c-b79f-35ed6cc5ab4b
To: /content/waiter_calling_model/yolov4-obj_best.weights
100% 256M/256M [00:04<00:00, 54.5M

In [3]:
!pip install mediapipe opencv-python

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.0/61.0 kB 2.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 35.6/35.6 MB 64.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 18.3/18.3 MB 108.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 294.9/294.9 kB 20.1 MB/s eta 0:00:00
  Attempting uninstall: protobuf
    Found existing installation: protobuf 5.29.5
    Uninstalling protobuf-5.29.5:
      Successfully uninstalled protobuf-5.29.5
  Attempting uninstall: numpy
    Found existing installation: numpy 2.0.2
    Uninstalling numpy-2.0.2:
      Successfully uninstalled numpy-2.0.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
thinc 8.3.6 requires numpy<3.0.0,>=2.0.0, but you have numpy 1.26.4 which is incompatible.
ydf 0.12.0 requires protobuf<6.0.0,>=5.29.1, but you have protobuf 4.25.8 which is incompatible.
grpcio

In [1]:
def show_local_mp4_video(file_name, width=640, height=480):
    import io
    import base64
    from IPython.display import HTML

    try:
        video_encoded = base64.b64encode(open(file_name, 'rb').read()).decode('ascii')
        return HTML(f'''
            <video width="{width}" height="{height}" controls>
                <source src="data:video/mp4;base64,{video_encoded}" type="video/mp4" />
                Your browser does not support the video tag.
            </video>''')
    except Exception as e:
        return HTML(f"<p> Error reading video {str(e)}</p>")


In [6]:
display(show_local_mp4_video('/content/video/desk_video.mp4', width=960, height=720))

# Working Detection of name

In [ ]:
import cv2
import numpy as np

# Load YOLOv4 model and class names
net = cv2.dnn.readNetFromDarknet("/content/yolov4-obj.cfg", "/content/yolov4-obj_best.weights")
classes = ['TANVIR', 'SHAFAYET', 'TOUFIQ', 'FAISAL', 'MUFRAD', 'ANIK', 'IMRAN', 'EMON']



# Open video and set up output writer
cap = cv2.VideoCapture('/content/video/desk_video.mp4')
frame_width, frame_height = int(cap.get(3)), int(cap.get(4))
fourcc = cv2.VideoWriter_fourcc(*'mp4v')
out = cv2.VideoWriter('/content/output_named_people.mp4', fourcc, 30, (frame_width, frame_height))




while True:
    success, frame = cap.read()
    if not success:
        break

    height, width, _ = frame.shape
    blob = cv2.dnn.blobFromImage(frame, 1/255, (416, 416), (0, 0, 0), swapRB=True, crop=False)

    net.setInput(blob)
    output_layers = net.getUnconnectedOutLayersNames()
    detections = net.forward(output_layers)

    boxes, confidences, class_ids = [], [], []

    for output in detections:
        for det in output:
            scores = det[5:]
            class_id = np.argmax(scores)
            confidence = scores[class_id]
            if confidence > 0.5:
                center_x = int(det[0] * width)
                center_y = int(det[1] * height)
                w = int(det[2] * width)
                h = int(det[3] * height)
                x = int(center_x - w / 2)
                y = int(center_y - h / 2)

                boxes.append([x, y, w, h])
                confidences.append(float(confidence))
                class_ids.append(class_id)

    indexes = cv2.dnn.NMSBoxes(boxes, confidences, 0.5, 0.4)
    font = cv2.FONT_HERSHEY_SIMPLEX
    colors = np.random.uniform(0, 255, size=(len(boxes), 3))

    if len(indexes) > 0:
        for i in indexes.flatten():
            x, y, w, h = boxes[i]
            label = str(classes[class_ids[i]])
            conf = str(round(confidences[i], 2))
            color = colors[i]
            cv2.rectangle(frame, (x, y), (x + w, y + h), color, 2)
            cv2.putText(frame, label + " " + conf, (x, y - 10), font, 0.8, color, 2)

    out.write(frame)

cap.release()
out.release()
print("✅ Saved output as 'output_named_people.mp4'")


✅ Saved output as 'output_named_people.mp4'


In [ ]:
from google.colab import files
files.download('/content/output_named_people.mp4')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

# fluctuating code with pose estimation

In [ ]:
import cv2
import numpy as np
import mediapipe as mp

# Load YOLOv4 model and class names
net = cv2.dnn.readNetFromDarknet("/content/yolov4-obj.cfg", "/content/yolov4-obj_best.weights")
classes = ['TANVIR', 'SHAFAYET', 'TOUFIQ', 'FAISAL', 'MUFRAD', 'ANIK', 'IMRAN', 'EMON']

# Initialize MediaPipe Pose
mp_pose = mp.solutions.pose
pose = mp_pose.Pose(static_image_mode=False, model_complexity=1, enable_segmentation=False, min_detection_confidence=0.5)

# Open video
cap = cv2.VideoCapture('/content/video/desk_video.mp4')
frame_width, frame_height = int(cap.get(3)), int(cap.get(4))
fourcc = cv2.VideoWriter_fourcc(*'mp4v')
out = cv2.VideoWriter('/content/output_named_people.mp4', fourcc, 30, (frame_width, frame_height))

while True:
    success, frame = cap.read()
    if not success:
        break

    height, width, _ = frame.shape
    blob = cv2.dnn.blobFromImage(frame, 1/255, (416, 416), (0, 0, 0), swapRB=True, crop=False)
    net.setInput(blob)
    output_layers = net.getUnconnectedOutLayersNames()
    detections = net.forward(output_layers)

    boxes, confidences, class_ids = [], [], []
    for output in detections:
        for det in output:
            scores = det[5:]
            class_id = np.argmax(scores)
            confidence = scores[class_id]
            if confidence > 0.5:
                center_x = int(det[0] * width)
                center_y = int(det[1] * height)
                w = int(det[2] * width)
                h = int(det[3] * height)
                x = int(center_x - w / 2)
                y = int(center_y - h / 2)
                boxes.append([x, y, w, h])
                confidences.append(float(confidence))
                class_ids.append(class_id)

    indexes = cv2.dnn.NMSBoxes(boxes, confidences, 0.5, 0.4)
    font = cv2.FONT_HERSHEY_SIMPLEX
    colors = np.random.uniform(0, 255, size=(len(boxes), 3))

    raised_hands_names = set()

    if len(indexes) > 0:
        for i in indexes.flatten():
            x, y, w, h = boxes[i]
            label = str(classes[class_ids[i]])
            conf = str(round(confidences[i], 2))
            color = colors[i]

            # Draw bounding box and label
            cv2.rectangle(frame, (x, y), (x + w, y + h), color, 2)
            cv2.putText(frame, label + " " + conf, (x, y - 10), font, 0.8, color, 2)

            # Extract ROI for pose detection
            x1, y1 = max(0, x), max(0, y)
            x2, y2 = min(width, x + w), min(height, y + h)
            person_roi = frame[y1:y2, x1:x2]

            # Convert ROI to RGB and run pose estimation
            roi_rgb = cv2.cvtColor(person_roi, cv2.COLOR_BGR2RGB)
            results = pose.process(roi_rgb)

            if results.pose_landmarks:
                landmarks = results.pose_landmarks.landmark

                # Map normalized landmarks to original ROI size
                def get_landmark_px(landmark):
                    return int(landmark.x * (x2 - x1)), int(landmark.y * (y2 - y1))

                left_wrist = get_landmark_px(landmarks[mp_pose.PoseLandmark.LEFT_WRIST])
                right_wrist = get_landmark_px(landmarks[mp_pose.PoseLandmark.RIGHT_WRIST])
                left_shoulder = get_landmark_px(landmarks[mp_pose.PoseLandmark.LEFT_SHOULDER])
                right_shoulder = get_landmark_px(landmarks[mp_pose.PoseLandmark.RIGHT_SHOULDER])

                # Check if either wrist is above the corresponding shoulder
                if (left_wrist[1] < left_shoulder[1]) or (right_wrist[1] < right_shoulder[1]):
                    raised_hands_names.add(label)

    # Display names in top-right corner
    y_offset = 30
    for name in sorted(raised_hands_names):
        cv2.putText(frame, f"{name} raised hand ✋", (frame_width - 300, y_offset), font, 0.7, (0, 255, 0), 2)
        y_offset += 30

    out.write(frame)

cap.release()
out.release()
pose.close()
print("✅ Saved output as 'output_named_people.mp4'")


✅ Saved output as 'output_named_people.mp4'


In [ ]:
import cv2
import numpy as np
import mediapipe as mp
from collections import deque, defaultdict

# Load YOLOv4 model and class names
net = cv2.dnn.readNetFromDarknet("/content/waiter_calling_model/yolov4-obj.cfg", "/content/waiter_calling_model/yolov4-obj_best.weights")
classes = ['TANVIR', 'SHAFAYET', 'TOUFIQ', 'FAISAL', 'MUFRAD', 'ANIK', 'IMRAN', 'EMON']

# Initialize MediaPipe Pose
mp_pose = mp.solutions.pose
pose = mp_pose.Pose(static_image_mode=False, model_complexity=1, enable_segmentation=False, min_detection_confidence=0.6)

# Open video and output
cap = cv2.VideoCapture('/content/video/desk_video.mp4')
frame_width, frame_height = int(cap.get(3)), int(cap.get(4))
fourcc = cv2.VideoWriter_fourcc(*'mp4v')
out = cv2.VideoWriter('/content/output_named_people.mp4', fourcc, 30, (frame_width, frame_height))

# Temporal history to smooth hand raise detection
raise_history = defaultdict(lambda: deque(maxlen=5))

while True:
    success, frame = cap.read()
    if not success:
        break

    height, width, _ = frame.shape
    blob = cv2.dnn.blobFromImage(frame, 1/255, (416, 416), (0, 0, 0), swapRB=True, crop=False)
    net.setInput(blob)
    output_layers = net.getUnconnectedOutLayersNames()
    detections = net.forward(output_layers)

    boxes, confidences, class_ids = [], [], []
    for output in detections:
        for det in output:
            scores = det[5:]
            class_id = np.argmax(scores)
            confidence = scores[class_id]
            if confidence > 0.5:
                center_x = int(det[0] * width)
                center_y = int(det[1] * height)
                w = int(det[2] * width)
                h = int(det[3] * height)
                x = int(center_x - w / 2)
                y = int(center_y - h / 2)
                boxes.append([x, y, w, h])
                confidences.append(float(confidence))
                class_ids.append(class_id)

    indexes = cv2.dnn.NMSBoxes(boxes, confidences, 0.5, 0.4)
    font = cv2.FONT_HERSHEY_SIMPLEX
    colors = np.random.uniform(0, 255, size=(len(boxes), 3))

    raised_hands_names = set()

    if len(indexes) > 0:
        for i in indexes.flatten():
            x, y, w, h = boxes[i]
            label = str(classes[class_ids[i]])
            conf = str(round(confidences[i], 2))
            color = colors[i]

            # Draw bounding box and label
            cv2.rectangle(frame, (x, y), (x + w, y + h), color, 2)
            cv2.putText(frame, label + " " + conf, (x, y - 10), font, 0.8, color, 2)

            # Add padding to improve detection quality
            pad = 20
            x1 = max(0, x - pad)
            y1 = max(0, y - pad)
            x2 = min(width, x + w + pad)
            y2 = min(height, y + h + pad)
            person_roi = frame[y1:y2, x1:x2]

            # Pose estimation
            roi_rgb = cv2.cvtColor(person_roi, cv2.COLOR_BGR2RGB)
            results = pose.process(roi_rgb)

            if results.pose_landmarks:
                landmarks = results.pose_landmarks.landmark

                def get_landmark_px(landmark):
                    return int(landmark.x * (x2 - x1)), int(landmark.y * (y2 - y1))

                left_wrist = get_landmark_px(landmarks[mp_pose.PoseLandmark.LEFT_WRIST])
                right_wrist = get_landmark_px(landmarks[mp_pose.PoseLandmark.RIGHT_WRIST])
                left_shoulder = get_landmark_px(landmarks[mp_pose.PoseLandmark.LEFT_SHOULDER])
                right_shoulder = get_landmark_px(landmarks[mp_pose.PoseLandmark.RIGHT_SHOULDER])

                # Check if either wrist is above the corresponding shoulder
                hand_raised = (left_wrist[1] < left_shoulder[1]) or (right_wrist[1] < right_shoulder[1])
                raise_history[label].append(hand_raised)

                # If raised in 3 of last 5 frames, consider raised
                if sum(raise_history[label]) >= 3:
                    raised_hands_names.add(label)

    # Display raised names on top-right corner
    y_offset = 30
    for name in sorted(raised_hands_names):
        cv2.putText(frame, f"{name} raised hand ✋", (frame_width - 320, y_offset), font, 0.8, (0, 255, 0), 2)
        y_offset += 35

    out.write(frame)

cap.release()
out.release()
pose.close()
print("✅ Saved output as 'output_named_people.mp4'")


✅ Saved output as 'output_named_people.mp4'


In [ ]:
import cv2
import numpy as np
import mediapipe as mp
import time
from collections import defaultdict

# Load YOLO model
net = cv2.dnn.readNetFromDarknet("/content/waiter_calling_model/yolov4-obj.cfg", "/content/waiter_calling_model/yolov4-obj_best.weights")
classes = ['TANVIR', 'SHAFAYET', 'TOUFIQ', 'FAISAL', 'MUFRAD', 'ANIK', 'IMRAN', 'EMON']

# MediaPipe Hands
mp_hands = mp.solutions.hands
hands = mp_hands.Hands(static_image_mode=False,
                       max_num_hands=2,
                       min_detection_confidence=0.5,
                       min_tracking_confidence=0.3)
mp_drawing = mp.solutions.drawing_utils

# Open video
cap = cv2.VideoCapture('/content/desk.mp4')
frame_width, frame_height = int(cap.get(3)), int(cap.get(4))
fourcc = cv2.VideoWriter_fourcc(*'mp4v')
out = cv2.VideoWriter('/content/output_named_people.mp4', fourcc, 30, (frame_width, frame_height))

# Keep last raised time
last_raised_time = defaultdict(lambda: 0)
DISPLAY_DURATION = 2  # seconds

while True:
    success, frame = cap.read()
    if not success:
        break

    timestamp = time.time()
    height, width, _ = frame.shape

    # YOLO detection
    blob = cv2.dnn.blobFromImage(frame, 1/255, (416, 416), swapRB=True, crop=False)
    net.setInput(blob)
    outputs = net.forward(net.getUnconnectedOutLayersNames())

    boxes, confidences, class_ids = [], [], []

    for output in outputs:
        for det in output:
            scores = det[5:]
            class_id = np.argmax(scores)
            confidence = scores[class_id]
            if confidence > 0.6:
                center_x, center_y = int(det[0] * width), int(det[1] * height)
                w, h = int(det[2] * width), int(det[3] * height)
                x, y = int(center_x - w / 2), int(center_y - h / 2)
                boxes.append([x, y, w, h])
                confidences.append(float(confidence))
                class_ids.append(class_id)

    indexes = cv2.dnn.NMSBoxes(boxes, confidences, 0.6, 0.4)
    font = cv2.FONT_HERSHEY_SIMPLEX

    if len(indexes) > 0:
        for i in indexes.flatten():
            x, y, w, h = boxes[i]
            label = classes[class_ids[i]]

            # Draw bounding box
            cv2.rectangle(frame, (x, y), (x + w, y + h), (255, 255, 0), 2)
            cv2.putText(frame, label, (x, y - 10), font, 0.8, (255, 255, 0), 2)

            # Crop person area
            x1 = max(0, x)
            y1 = max(0, y)
            x2 = min(width, x + w)
            y2 = min(height, y + h)
            person_roi = frame[y1:y2, x1:x2].copy()

            # Convert for MediaPipe
            person_rgb = cv2.cvtColor(person_roi, cv2.COLOR_BGR2RGB)
            results = hands.process(person_rgb)

            hand_raised = False

            if results.multi_hand_landmarks:
                for hand_landmarks in results.multi_hand_landmarks:
                    mp_drawing.draw_landmarks(person_roi, hand_landmarks, mp_hands.HAND_CONNECTIONS)

                    for lm in hand_landmarks.landmark:
                        y_px = int(lm.y * (y2 - y1))
                        if y_px < h * 0.3:  # Hand is in upper 30% of person box
                            hand_raised = True
                            break


            if hand_raised:
                last_raised_time[label] = timestamp

            # Replace back the drawn ROI
            frame[y1:y2, x1:x2] = person_roi

    # Display raised hand names (top-right)
    y_offset = 30
    for name in classes:
        if timestamp - last_raised_time[name] < DISPLAY_DURATION:
            cv2.putText(frame, f"{name} raised hand", (frame_width - 330, y_offset), font, 0.8, (0, 255, 0), 2)
            y_offset += 35

    out.write(frame)

cap.release()
out.release()
hands.close()
print("✅ Saved output as 'output_named_people.mp4'")


KeyboardInterrupt: 

In [ ]:
from IPython.display import display
display(show_local_mp4_video('/content/output_named_people.mp4'))

Working fine, need more refinement

# far better

In [ ]:
import cv2
import numpy as np
import mediapipe as mp
import time
from collections import defaultdict

net.setPreferableBackend(cv2.dnn.DNN_BACKEND_CUDA)
net.setPreferableTarget(cv2.dnn.DNN_TARGET_CUDA)


# Load YOLO model
net = cv2.dnn.readNetFromDarknet(
    "/content/waiter_calling_model/yolov4-obj.cfg",
    "/content/waiter_calling_model/yolov4-obj_best.weights"
)
classes = ['TANVIR', 'SHAFAYET', 'TOUFIQ', 'FAISAL', 'MUFRAD', 'ANIK', 'IMRAN', 'EMON']


# MediaPipe Hands
mp_hands = mp.solutions.hands
hands = mp_hands.Hands(static_image_mode=False,
                       max_num_hands=2,
                       min_detection_confidence=0.5,
                       min_tracking_confidence=0.3)
mp_drawing = mp.solutions.drawing_utils

# Video input/output
cap = cv2.VideoCapture('/content/video/desk_video.mp4')
frame_width, frame_height = int(cap.get(3)), int(cap.get(4))
fourcc = cv2.VideoWriter_fourcc(*'mp4v')
out = cv2.VideoWriter('/content/output_named_people.mp4', fourcc, 30, (frame_width, frame_height))

# Last raised hand tracking
last_raised_time = defaultdict(lambda: 0)
DISPLAY_DURATION = 2.5  # seconds

while True:
    success, frame = cap.read()
    if not success:
        break

    timestamp = time.time()
    height, width, _ = frame.shape

    # YOLO person detection
    blob = cv2.dnn.blobFromImage(frame, 1/255, (416, 416), swapRB=True, crop=False)
    net.setInput(blob)
    outputs = net.forward(net.getUnconnectedOutLayersNames())

    boxes, confidences, class_ids = [], [], []

    for output in outputs:
        for det in output:
            scores = det[5:]
            class_id = np.argmax(scores)
            confidence = scores[class_id]
            if confidence > 0.6:
                center_x, center_y = int(det[0] * width), int(det[1] * height)
                w, h = int(det[2] * width), int(det[3] * height)
                x = int(center_x - w / 2)
                y = int(center_y - h / 2)
                boxes.append([x, y, w, h])
                confidences.append(float(confidence))
                class_ids.append(class_id)

    indexes = cv2.dnn.NMSBoxes(boxes, confidences, 0.6, 0.4)
    hand_raised_name = None  # Only one per frame

    if len(indexes) > 0:
        for i in indexes.flatten():
            if hand_raised_name is not None:
                break  # Skip others once one raised hand is detected

            x, y, w, h = boxes[i]
            label = classes[class_ids[i]]

            # Crop person box
            x1 = max(0, x)
            y1 = max(0, y)
            x2 = min(width, x + w)
            y2 = min(height, y + h)
            person_roi = frame[y1:y2, x1:x2].copy()

            # Hand detection
            roi_rgb = cv2.cvtColor(person_roi, cv2.COLOR_BGR2RGB)
            results = hands.process(roi_rgb)

            if results.multi_hand_landmarks:
                for hand_landmarks in results.multi_hand_landmarks:
                    mp_drawing.draw_landmarks(person_roi, hand_landmarks, mp_hands.HAND_CONNECTIONS)

                    for lm in hand_landmarks.landmark:
                        y_px = int(lm.y * (y2 - y1))
                        if y_px < h * 0.3:  # hand near top
                            last_raised_time[label] = timestamp
                            hand_raised_name = label
                            break

                # Put drawn hand back to frame
                frame[y1:y2, x1:x2] = person_roi

    # Show only one name at a time
    for name in classes:
        if timestamp - last_raised_time[name] < DISPLAY_DURATION:
            cv2.putText(frame, f"{name}", (frame_width-330, 60),
                        cv2.FONT_HERSHEY_SIMPLEX, 1.2, (0, 0, 255), 3)
            break  # Only show one name

    out.write(frame)

cap.release()
out.release()
hands.close()

In [ ]:
from google.colab import files
files.download('/content/output_named_people.mp4')

In [7]:
display(show_local_mp4_video('/content/output_named_people.mp4', width=960, height=720))

# 1 second freez

In [35]:
import cv2
import numpy as np
import mediapipe as mp
import time
from collections import defaultdict

# Load YOLO model
net = cv2.dnn.readNetFromDarknet(
    "/content/waiter_calling_model/yolov4-obj.cfg",
    "/content/waiter_calling_model/yolov4-obj_best.weights"
)
classes = ['TANVIR', 'SHAFAYET', 'TOUFIQ', 'FAISAL', 'MUFRAD', 'ANIK', 'IMRAN', 'EMON']

# MediaPipe Hands
mp_hands = mp.solutions.hands
hands = mp_hands.Hands(static_image_mode=False,
                       max_num_hands=2,
                       min_detection_confidence=0.5,
                       min_tracking_confidence=0.3)
mp_drawing = mp.solutions.drawing_utils

# Video input/output
cap = cv2.VideoCapture('/content/desk_2.mp4')
frame_width, frame_height = int(cap.get(3)), int(cap.get(4))
fourcc = cv2.VideoWriter_fourcc(*'mp4v')
out = cv2.VideoWriter('/content/output_named_people.mp4', fourcc, 30, (frame_width, frame_height))

# Track most recent raised hand info
last_hand_name = None
last_hand_time = 0
FREEZE_DURATION = 2  # seconds

while True:
    success, frame = cap.read()
    if not success:
        break

    timestamp = time.time()
    height, width, _ = frame.shape

    # If we're still within freeze period, just draw the last detected name and skip detection
    if last_hand_name and (timestamp - last_hand_time < FREEZE_DURATION):
        cv2.putText(frame, f"{last_hand_name}", (frame_width - 330, 60),
                    cv2.FONT_HERSHEY_SIMPLEX, 1.2, (0, 0, 255), 3)
        out.write(frame)
        continue

    # YOLO person detection
    blob = cv2.dnn.blobFromImage(frame, 1/255, (416, 416), swapRB=True, crop=False)
    net.setInput(blob)
    outputs = net.forward(net.getUnconnectedOutLayersNames())

    boxes, confidences, class_ids = [], [], []

    for output in outputs:
        for det in output:
            scores = det[5:]
            class_id = np.argmax(scores)
            confidence = scores[class_id]
            if confidence > 0.6:
                center_x, center_y = int(det[0] * width), int(det[1] * height)
                w, h = int(det[2] * width), int(det[3] * height)
                x = int(center_x - w / 2)
                y = int(center_y - h / 2)
                boxes.append([x, y, w, h])
                confidences.append(float(confidence))
                class_ids.append(class_id)

    indexes = cv2.dnn.NMSBoxes(boxes, confidences, 0.6, 0.4)
    hand_detected_this_frame = False

    if len(indexes) > 0:
        for i in indexes.flatten():
            if hand_detected_this_frame:
                break  # Skip others after one detection

            x, y, w, h = boxes[i]
            label = classes[class_ids[i]]

            # Crop person box
            x1 = max(0, x)
            y1 = max(0, y)
            x2 = min(width, x + w)
            y2 = min(height, y + h)
            person_roi = frame[y1:y2, x1:x2].copy()

            # Hand detection
            roi_rgb = cv2.cvtColor(person_roi, cv2.COLOR_BGR2RGB)
            results = hands.process(roi_rgb)

            if results.multi_hand_landmarks:
                for hand_landmarks in results.multi_hand_landmarks:
                    for lm in hand_landmarks.landmark:
                        y_px = int(lm.y * (y2 - y1))
                        if y_px < h * 0.3:  # hand near top
                            last_hand_name = label
                            last_hand_time = timestamp
                            hand_detected_this_frame = True
                            break

                frame[y1:y2, x1:x2] = person_roi  # Draw updated hand landmarks

    # Show current raised name if any
    if last_hand_name and (timestamp - last_hand_time < FREEZE_DURATION):
        cv2.putText(frame, f"{last_hand_name}", (frame_width - 330, 60),
                    cv2.FONT_HERSHEY_SIMPLEX, 1.2, (0, 0, 255), 3)

    out.write(frame)

cap.release()
out.release()
hands.close()
print("✅ Saved output as 'output_named_people.mp4'")


✅ Saved output as 'output_named_people.mp4'
